In [1]:
# Normal packages
import geopandas as gpd
import numpy as np
import pandas as pd

# Import warnings
import warnings
warnings.filterwarnings("ignore")

# Format
from babel.numbers import format_currency
from calitp import to_snakecase

# Display
from IPython.display import HTML, Image, Markdown, display, display_html

# Settings
pd.options.display.max_columns = 100
pd.set_option("display.max_rows", None)
pd.set_option("display.max_colwidth", None)
pd.options.display.float_format = "{:,.2f}".format

# GCS, del later since this will presumbly be read from a script that cleans up the data
GCS_FILE_PATH = "gs://calitp-analytics-data/data-analyses/project_prioritization/"
FILE = "fake_data.xlsx"

# My utilities
import _utils

/opt/conda/lib/python3.10/site-packages/geopandas/_compat.py:112: UserWarning: The Shapely GEOS version (3.10.3-CAPI-1.16.1) is incompatible with the GEOS version PyGEOS was compiled with (3.10.1-CAPI-1.16.0). Conversions between both will be slow.
  warnings.warn(


In [2]:
df = pd.read_excel(f"{GCS_FILE_PATH}{FILE}", sheet_name="fake")

In [3]:
# Parameter Cell
district = 8

In [4]:
# Copy of original unfiltered df
df_full = df.copy()

# df with project that was set in the parameter cell
df = df.loc[df["district"] == district].reset_index(drop=True)

In [5]:
# Summary tables
# Count of projects by phases it is in
phases_df = _utils.summarize_by_project_names(df, "current_phase")

# Count of projects whether it is rural or urban
rural_urban_df = _utils.summarize_by_project_names(df, "urban_rural")

# Count of projects by district
districts_df = _utils.summarize_by_project_names(df, "district_full_name")

# Count of projects by district - for mapping
districts_gdf = _utils.summarize_by_project_names(df_full, "district")

# Count of projects by project type
projects_df = _utils.summarize_by_project_names(df, "primary_mode")

# Count of projects by lead agency
agency_df = _utils.summarize_by_project_names(df, "lead_agency")

In [6]:
# Objects
# Median benefit score
median_benefit_score = int(df.fake_benefit_score.median())

# Total Requested Funds
total_cost = format_currency(
    (df["total_project_cost__$1,000_"].sum()),
    currency="USD",
)

# Median project cost
median_cost = format_currency(
    (df["total_project_cost__$1,000_"].median()),
    currency="USD",
)

# Total Requested Funds
total_req = format_currency(
    (df["current_fake_fund_requested"].sum()),
    currency="USD",
)

# Median Requested Funds
median_req = format_currency(
    (df["current_fake_fund_requested"].median()),
    currency="USD",
)

In [7]:
display(
    Markdown(
        f"""<h1>{df.district_full_name[0]} District Summary</h1>
        <li><b>{total_req}</b> in total funds requested across all the agencies.
        <li>The total cost of all the projects is <b>{total_cost}</b>.
        <li>There are a total of <b>{districts_df['Total Projects'][0]}</b> projects.
        <li>The most common project category is <b>{projects_df['Primary Mode'][0]}</b>.
        <li>Most projects are in the <b>{phases_df['Current Phase'][0]}</b> phase.
        <li><b>{median_benefit_score}</b> is the median benefit score.
        
        """
    )
)

<h1>08 - San Bernardino Project Summary</h1>
        <li><b>$19,749,359.78</b> in total funds requested across all the agencies.
        <li>The total cost of all the projects is <b>$31,390,166.00</b>.
        <li>There are a total of <b>68</b> projects.
        <li>The most common project category is <b>Highway</b>.
        <li>Most projects are in the <b>NONE</b> phase.
        <li><b>9</b> is the median benefit score.
        
        

In [8]:
display(
    Markdown(
        f"""<h2>Rural versus Urban</h2>
        Most projects are in an <b>{rural_urban_df['Urban Rural'][0]}</b> area, 
        totaling to <b>{rural_urban_df['Total Project ($1000) Formatted'][0]}</b>. 
        """
    )
)

<h2>Rural versus Urban</h2>
        Most projects are in an <b>Urban</b> area, 
        totaling to <b>$28,985,454.00</b>. 
        

In [9]:
total_urban_rural_bar = _utils.basic_bar_chart_custom_tooltip(
    rural_urban_df,
    "Total Project Cost  $1,000",
    "Urban Rural",
    "Total Project ($1000) Formatted",
    "Urban Rural",
    "Cost of Projects",
)

In [10]:
total_urban_rural_pie = _utils.basic_pie_chart(
    rural_urban_df,
    "Total Projects:Q",
    "Urban Rural:N",
    "Total Projects",
    "Total Projects",
)

In [11]:
total_urban_rural_bar | total_urban_rural_pie

alt.HConcatChart(...)

In [12]:
display(
    Markdown(
        f"""<h2>District Map Comparison</h2>
        """
    )
)

<h2>District Map Comparison</h2>
        

In [13]:
districts_gdf = _utils.create_caltrans_map(districts_gdf)

In [14]:
districts_gdf.explore(
    "Total Projects",
    cmap="GnBu",
    width=500,
    height=500,
    tooltip=["District", "Total Projects", "Total Project ($1000) Formatted"],
    highlight=True,
    legend=False,
    style_kwds={"fillOpacity": 1},
)

In [15]:
display(
    Markdown(
        f"""<h2>Project Categories</h2>
        Looking at project categories by Total Project Cost and Total Project count.
        """
    )
)

<h2>Project Categories</h2>
        Looking at project categories by Total Project Cost and Total Project count.
        

In [16]:
project_bar_cost = _utils.basic_bar_chart_custom_tooltip(
    projects_df,
    "Total Project Cost  $1,000",
    "Primary Mode",
    "Total Project ($1000) Formatted",
    "Primary Mode",
    "Project Category by Cost",
)

In [17]:
project_bar_total = _utils.basic_bar_chart_custom_tooltip(
    projects_df,
    "Total Projects",
    "Primary Mode",
    "Total Projects",
    "Primary Mode",
    "Project Category by Total Projects",
)

In [18]:
project_bar_cost | project_bar_total

alt.HConcatChart(...)

In [19]:
display(
    Markdown(
        f"""<h2>All Projects</h2>
        A list of all the projects ranked by benefit score.
        """
    )
)

<h2>All Projects</h2>
        A list of all the projects ranked by benefit score.
        

In [20]:
# Subset
df_subset = df[
    [
        "district_rank",
        "fake_benefit_score",
        "lead_agency",
        "primary_mode",
        "project_name",
        "current_fake_fund_requested",
        "total_project_cost__$1,000_",
    ]
]

# Format
df_subset["total_project_cost__$1,000_"] = df_subset[
    "total_project_cost__$1,000_"
].apply(lambda x: format_currency(x, currency="USD", locale="en_US"))

df_subset["current_fake_fund_requested"] = df_subset[
    "current_fake_fund_requested"
].apply(lambda x: format_currency(x, currency="USD", locale="en_US"))
df["fake_benefit_score"] = df["fake_benefit_score"].apply(lambda x: round(x, 2))

# Clean up Col Names
df_subset = _utils.clean_up_columns(df_subset)

# Sort by rank
df_subset = df_subset.sort_values("District Rank")

In [21]:
_utils.styled_df(df_subset)

In [22]:
display(
    Markdown(
        f"""<h2>Lead Agencies</h2>
        There are {len(agency_df)} unique agencies in this data set. <b>{agency_df['Lead Agency'][0]}</b> is the agency 
        with the most projects. The table below is organized from greatest to least number of projects. 
        """
    )
)

<h2>Lead Agencies</h2>
        There are 12 unique agencies in this data set. <b>None</b> is the agency 
        with the most projects. The table below is organized from greatest to least number of projects. 
        

In [23]:
_utils.styled_df(agency_df)